# Tutorial 3: Calculate climate-sensitive R0 for malaria transmission
In this tutorial you will:  
1. Query PAIRS for a point location for temperature and rainfall  
2. Aggregate and reformat the output to a pandas dataframe with means for both variables for each day  
3. Calculate climate-dependent components of malaria transmission  
4. Combine components to calculate R0  
5. Create various interactive plots using plotly  

# Background
The R0 model equation used here is based on the structure of LMM, the Liverpool Malaria Model, a dynamic compartmental model with susceptible, exposed and infectious categories for human and mosquito populations (Hoshen and Morse, 2005; Ermert et al., 2011). This version of the model has been used in climate change malaria assessments (e.g. Caminade et al., 2014)

The expression for $R_0$ is given by:

$$R_0 = \frac{ma^{2}bc}{\mu r} exp(-\mu\tau_y - r \tau_x)$$


Where:  $b, c, r$, and $\tau_x$ are climate-independent parameters:  
  
$b$ is the human inoculation efficiency   
$c$ is the mosquito inoculation efficiency  
$r$ is the human recovery rate  
$\tau_x$ is the latent period in human (time taken to become infectious once infected).  

$a$, $\mu$, $\tau_y$ and $m$ are all climate-dependent parameters, calculated from daily temperature, $T$ and rainfall $R$:  
  
#### Biting rate
Biting rate $a$ is given by:   

$$a = HBI\frac{(T - T_g)}{D_g}$$  

where $T_g$ and $D_g$ are the parameters for the gonotrophic cycle.  
  
  
#### Mosquito mortality
Adult mosquito mortality, $\mu$ is parameterised by two alternative formulations, which calculate daily survival probability $P = \frac{1}{\mu}$:      
First, the original mortality function used in Hoshen and Morse (2004):

$$P = 0.45 + 0.054T + 0.0016T^{2}$$

Second, the equation used in Craig et al. (1999):

$$P = exp \left( \frac{-1.0}{-4.4 + 1.31T - 0.03T^{2}} \right)$$


#### Sporogonic Cycle
The sporogonic cycle length, $\tau_y$ is given by the expression:  

$$\tau_y = \frac{D_s}{(T - T_s)}$$

where $T_g$ and $D_g$ are the parameters for the sporogonic cycle.  

#### Vector density
Vector density (adult females per human), $m$ is calculated using a simple model in which the mosquito population on day i grows according to a linear function of the rainfall over the past $n$ days:     

$$m_i = m_{i-1}\cdot\frac{A}{N}\left(\sum_{d=i-n+1}^{i}R_i\right) + B$$

where $R_i$ is the rainfall on day $i$, $A$, and $B$ are constants and $N$ is the human population size.



**References**  
Morse, A. P., Doblas-Reyes, F. J., Hoshen, M. B., Hagedorn, R., & Palmer, T. N. (2005). A forecast quality assessment of an end-to-end probabilistic multi-model seasonal forecast system using a malaria model. TELLUS SERIES A-DYNAMIC METEOROLOGY AND OCEANOGRAPHY, 57(3), 464-475. [doi:10.1111/j.1600-0870.2005.00124.x](https://onlinelibrary.wiley.com/doi/full/10.1111/j.1600-0870.2005.00124.x)

Craig, M.H., Snow, R. W., and le Seur, D. (1999). A Climate-based Distribution Model of Malaria Transmission in Sub-Saharan Africa. PARASITOLOGY TODAY, 15:3. [doi.org/10.1016/S0169-4758(99)01396-4](https://www.sciencedirect.com/science/article/pii/S0169475899013964)

Ermert, V., Fink, A. H., Jones, A. E., & Morse, A. P. (2011). Development of a new version of the Liverpool Malaria Model. I. Refining the parameter settings and mathematical formulation of basic processes based on a literature review. MALARIA JOURNAL, 10. [doi:10.1186/1475-2875-10-35](https://malariajournal.biomedcentral.com/articles/10.1186/1475-2875-10-35)

Caminade, C., Kovats, S., Rocklov, J., Tompkins, A. M., Morse, A. P., Jesus Colon-Gonzalez, F., . . . Lloyd, S. J. (2014). Impact of climate change on global malaria distribution. Proceedings of the National Academy of Sciences, 111(9), 3286-3291. [doi:10.1073/pnas.1302089111](https://www.pnas.org/content/pnas/111/9/3286.full.pdf)

# Preparatory steps

### Set up Watson studio project token - replace this with a cell generated for your Watson Studio project

In [ ]:
# @hidden_cell
# The project token is an authorization token that is used to access project resources like data sources, connections, and used by platform APIs.
from project_lib import Project
project = Project(project_id='8391dedf-3411-4c70-a9b7-12c7bfb8bba9', project_access_token='p-c1517bfd8cb5033953111273e5f9936f6aac23ff')
pc = project.project_context

### Install the PAIRS api library  

In [ ]:
!pip install ibmpairs

### Load the required libraries  

In [5]:
import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt
from datetime import datetime

# Retrieve time series data from PAIRS 

### Connect to PAIRS

In [8]:
from ibmpairs import paw, authentication
my_file = project.get_file("pairspass-annejones.txt") 
PAIRS_API_KEY=my_file.readline().decode('utf-8') 
PAIRS_USER = "anne.jones@ibm.com" # REPLACE WITH YOUR USERNAME
PAIRS_SERVER = "https://pairs.res.ibm.com"
OAUTH = authentication.OAuth2(api_key = PAIRS_API_KEY )

### Create dictionary to store the layer ids we may want to use

In [2]:
pairs_dict = {
    'ERA5 temperature' : 49423,
    'ERA5 rainfall' : 49459,
    'CHIRPS rainfall' : 49316,
    'SEDAC population' : 48774
}

### Select a location for which we want to run the model

In [10]:
lat = -24.0
lon = 29.0

### Create point query json

In [11]:
query_json = {
      "layers" : [
          {"type" : "raster", "id" : pairs_dict["ERA5 temperature"]},
          {"type" : "raster", "id" : pairs_dict["ERA5 rainfall"]}
      ],
      "spatial" : {"type" : "point",  "coordinates" : [str(lat), str(lon)]}, # [latitude, longitude]
      "temporal" : {"intervals" : [
          {"start" : "2001-01-01T00:00:00Z", "end" : "2021-01-01T00:00:00Z"}
      ]}
  }

In [12]:
# create query object
query = paw.PAIRSQuery(query_json, PAIRS_SERVER,  auth=OAUTH, authType='api-key') 
# submit the query
query.submit()

GeoPandas not available on your system. Cannot convert vector dataframe to GeoPandas dataframe.


In [52]:
# check the data returned
query.vdf.head()

layerId                 timestamp  longitude  latitude  value  region  \
350635    49459 2020-12-31 20:00:00+00:00       29.0     -24.0    0.0     NaN   
350636    49459 2020-12-31 21:00:00+00:00       29.0     -24.0    0.0     NaN   
350637    49459 2020-12-31 22:00:00+00:00       29.0     -24.0    0.0     NaN   
350638    49459 2020-12-31 23:00:00+00:00       29.0     -24.0    0.0     NaN   
350639    49459 2021-01-01 00:00:00+00:00       29.0     -24.0    0.0     NaN   

        property        geometry       var  day  month  year  
350635       NaN  POINT (29 -24)  rainfall   31     12  2020  
350636       NaN  POINT (29 -24)  rainfall   31     12  2020  
350637       NaN  POINT (29 -24)  rainfall   31     12  2020  
350638       NaN  POINT (29 -24)  rainfall   31     12  2020  
350639       NaN  POINT (29 -24)  rainfall    1      1  2021

# Post-processing of the queried data

### Add variable name to the dataframe for ease of use

In [14]:
query.vdf['var'] = None
query.vdf.loc[query.vdf['layerId']==pairs_dict["ERA5 temperature"], 'var'] = 'temperature'
query.vdf.loc[query.vdf['layerId']==pairs_dict["ERA5 rainfall"], 'var'] = 'rainfall'

### Add consituents of date

In [15]:
query.vdf['day'] = query.vdf['timestamp'].dt.day
query.vdf['month'] = query.vdf['timestamp'].dt.month
query.vdf['year'] = query.vdf['timestamp'].dt.year
query.vdf.head()

layerId                 timestamp  longitude  latitude       value  region  \
0    49423 2001-01-01 01:00:00+00:00       29.0     -24.0  292.941559     NaN   
1    49423 2001-01-01 02:00:00+00:00       29.0     -24.0  292.840912     NaN   
2    49423 2001-01-01 03:00:00+00:00       29.0     -24.0  294.811737     NaN   
3    49423 2001-01-01 04:00:00+00:00       29.0     -24.0  293.836121     NaN   
4    49423 2001-01-01 05:00:00+00:00       29.0     -24.0  293.257843     NaN   

   property        geometry          var  day  month  year  
0       NaN  POINT (29 -24)  temperature    1      1  2001  
1       NaN  POINT (29 -24)  temperature    1      1  2001  
2       NaN  POINT (29 -24)  temperature    1      1  2001  
3       NaN  POINT (29 -24)  temperature    1      1  2001  
4       NaN  POINT (29 -24)  temperature    1      1  2001

### Aggregate to daily data and transform to temperature in degrees Celcius and rainfall in mm

In [16]:
query.vdf.loc[query.vdf['var']=='temperature', 'value'] = query.vdf.loc[query.vdf['var']=='temperature', 'value'] - 273.15
query.vdf.loc[query.vdf['var']=='rainfall', 'value'] = query.vdf.loc[query.vdf['var']=='rainfall', 'value']*1000.0 # native units are m per hour

In [17]:
vars_agg = query.vdf.groupby(['layerId', 'day', 'month', 'year', 'longitude', 'latitude', 'var'], as_index=False).aggregate('mean')
vars_agg

layerId  day  month  year  longitude  latitude          var      value  \
0        49423    1      1  2001       29.0     -24.0  temperature  22.233392   
1        49423    1      1  2002       29.0     -24.0  temperature  25.498193   
2        49423    1      1  2003       29.0     -24.0  temperature  21.804725   
3        49423    1      1  2004       29.0     -24.0  temperature  20.897620   
4        49423    1      1  2005       29.0     -24.0  temperature  24.388575   
...        ...  ...    ...   ...        ...       ...          ...        ...   
14607    49459   31     12  2016       29.0     -24.0     rainfall   0.426114   
14608    49459   31     12  2017       29.0     -24.0     rainfall   0.005349   
14609    49459   31     12  2018       29.0     -24.0     rainfall   0.084506   
14610    49459   31     12  2019       29.0     -24.0     rainfall   0.015481   
14611    49459   31     12  2020       29.0     -24.0     rainfall   0.011243   

       region  property  
0         NaN       NaN  
1         NaN       NaN  
2         NaN       NaN  
3         NaN       NaN  
4         NaN       NaN  
...       ...       ...  
14607     NaN       NaN  
14608     NaN       NaN  
14609     NaN       NaN  
14610     NaN       NaN  
14611     NaN       NaN  

[14612 rows x 10 columns]

### Convert rainfall to mm per day

In [18]:
vars_agg.loc[vars_agg['var']=='rainfall', 'value'] = vars_agg.loc[vars_agg['var']=='rainfall', 'value']*24.0

### Convert the dataframe to "wide" format i.e. multiple variables for the same date

In [48]:
cols_to_keep = ['day', 'month', 'year', 'longitude', 'latitude']
vars_wide = vars_agg[vars_agg['var']=='rainfall'].copy().reset_index(drop=True)
vars_wide.rename(columns = {'value': 'rainfall'}, inplace=True)
vars_wide.drop(columns=['var', 'region', 'property', 'layerId'], inplace=True)

vars_wide2 = vars_agg[vars_agg['var']=='temperature'].copy().reset_index(drop=True)
vars_wide2.rename(columns = {'value': 'temperature'}, inplace=True)
vars_wide2.drop(columns=['var', 'region', 'property','layerId'], inplace=True)

print(len(vars_agg), len(vars_wide), len(vars_wide2))

vars_wide = vars_wide.merge(vars_wide2, how = 'inner', on = ['day', 'month', 'year', 'longitude', 'latitude'])
df = vars_wide

14612 7306 7306


In [49]:
df.head()

day  month  year  longitude  latitude  rainfall  temperature
0    1      1  2001       29.0     -24.0  6.687416    22.233392
1    1      1  2002       29.0     -24.0  0.004647    25.498193
2    1      1  2003       29.0     -24.0  0.000000    21.804725
3    1      1  2004       29.0     -24.0  1.721056    20.897620
4    1      1  2005       29.0     -24.0  2.637308    24.388575

# Prepare the model 
### Create a dictionary to store the model parameters

In [4]:
params = { "b": 0.5, # inoculation efficiency for humans
    "c" : 1.0, # inoculation effiency for mosquitoes
    "hia" : 15.0, # human latent period (days)
    "r" : 0.0284, # human recovery rate (per day)
    "rainfall_multiplier" : 1.0, # rainfall to mosquito linear multiplication factor (per day)
    "rainfall_offset" : 0.0, # rainfall to mosquito offset
    "hbi" : 0.5, # human blood index
    "Tg" : 9.0, #  Gonotrophic threshold temperature 
    "Dg" : 37.0, # Gonotrophic cycle length in degree days
    "Ts" : 18.0, # Sporogonic threshold temperature 
    "Ds" : 111.0, # Sporoogonic cycle length in degree days
    "stype" : "martens" # Survival type (valid values are 0 = Martens, 2 = Craig)
}

# Calculate Mosquito population survival per day

### We define a function which calculates survival probability for a given temperature

In [5]:
# stype is an text string specifying the type of mosquito survival scheme
# T is a multidimensional array e.g. [x, y, month]
# The function calculates element-wise survival probability
def mos_survival(stype, T):
    if stype=="martens":
        # Origin Martens as used in default LMM settings - see Hoshen and Morse (2004)
        p = 0.45 + 0.054*T - 0.0016*np.square(T)
        p[p < 0.0] = 0.0
        p[T > 40.0] =0.0
    elif stype=="craig":
         # Craig/Martens from Craig et al [add ref]
        p = np.exp(-1.0/(-4.4+1.31*T-0.03*np.square(T)))
        p[T<4.0] = 0.0
        p[T>39.9] = 0.0
        p[p<0.0] = 0.0
    else:
        print("error - survival type not recognised")
        return None
    p[p>1.0]=1.0
    return p

### Use the function to calculate P for the temperature data

In [50]:
df['P'] = mos_survival(params['stype'], df['temperature'].values)

In [51]:
df.head()

day  month  year  longitude  latitude  rainfall  temperature         P
0    1      1  2001       29.0     -24.0  6.687416    22.233392  0.859685
1    1      1  2002       29.0     -24.0  0.004647    25.498193  0.786650
2    1      1  2003       29.0     -24.0  0.000000    21.804725  0.866742
3    1      1  2004       29.0     -24.0  1.721056    20.897620  0.879735
4    1      1  2005       29.0     -24.0  2.637308    24.388575  0.815299

### Visualise the output

# Calculate Gonotrophic and Sporogonic cycle lengths

### Define functions to calculate Gonotrophic and sporogonic cycles

In [54]:
# T is a multidimensional array e.g. [x, y, month]
# the remaining arguments are constants
# Calculates element-wise cycle length in days
def gono_length(T, Dg, Tg):
    Gdays = np.ones(T.shape)*1000.0
    idx = T>Tg
    Gdays[idx] = 1.0 + np.divide(Dg, (T[idx] - Tg))
    return Gdays

def sporo_length(T, Ds, Ts):
    Sdays = np.ones(T.shape)*1000.0
    idx = T>Ts
    Sdays[idx] = np.divide(Ds, (T[idx] - Ts))

    return Sdays

### Use the functions to calculate the cycle lenghts for the temperature data

In [56]:
df['gono_len'] = gono_length(df['temperature'].values, params['Dg'], params['Tg'])

In [57]:
df.head()

day  month  year  longitude  latitude  rainfall  temperature         P  \
0    1      1  2001       29.0     -24.0  6.687416    22.233392  0.859685   
1    1      1  2002       29.0     -24.0  0.004647    25.498193  0.786650   
2    1      1  2003       29.0     -24.0  0.000000    21.804725  0.866742   
3    1      1  2004       29.0     -24.0  1.721056    20.897620  0.879735   
4    1      1  2005       29.0     -24.0  2.637308    24.388575  0.815299   

   gono_len  
0  3.795957  
1  3.242670  
2  3.889558  
3  4.109866  
4  3.404381

In [58]:
df['sporo_len'] = sporo_length(df['temperature'].values, params['Ds'], params['Ts'])

In [59]:
df.head()

day  month  year  longitude  latitude  rainfall  temperature         P  \
0    1      1  2001       29.0     -24.0  6.687416    22.233392  0.859685   
1    1      1  2002       29.0     -24.0  0.004647    25.498193  0.786650   
2    1      1  2003       29.0     -24.0  0.000000    21.804725  0.866742   
3    1      1  2004       29.0     -24.0  1.721056    20.897620  0.879735   
4    1      1  2005       29.0     -24.0  2.637308    24.388575  0.815299   

   gono_len  sporo_len  
0  3.795957  26.220107  
1  3.242670  14.803566  
2  3.889558  29.174253  
3  4.109866  38.307299  
4  3.404381  17.374765

### Visualise the output

# Calculate the Mosquito population

### Define a function to calculate mosquito population
New mosquitoes are added as a linear function of total rainfall over the previous n timesteps  

In [88]:
# Arguments p and rain must be 3 dimensional arrays 
# of the same shape [x, y, t] or [y, x, t]
# The last dimension is assumed to be time
# Returns an array of mosquito population size, of the same
# shape as input
# steplen, rainmult, rainoffset are constants
# mos0 is the number of mosquitoes at the first timestep
def calc_mosquito_pop(mos0, p, rain, steplen, rainmult, rainoffset, n=10):
    if not (rain.shape==p.shape):
        print("error: supplied array shapes do not match")
        return None
    # grow mosquito population according to rainfall each timestep
    dims = p.shape
    if len(dims)!=3:
        print("error: arrays must have 3 dimensions")
        return None
    mosquitoes = np.empty(dims)
    mosquitoes[0] = mos0
    nt = dims[len(dims)-1]
    # loop over time to simulate population dynamics
    for i in range(1, nt):
        istart = max(0, i-n+1)
        #print(istart)
        rainacc = np.mean(rain[:,:,istart:i], axis=2)
        #print(rainacc)
        mosquitoes[:,:,i] = mosquitoes[:,:,i-1]*np.power(p[:,:,i-1], steplen) + \
                    rainmult*rainacc + rainoffset
    mosquitoes[mosquitoes<0.0] = 0.0
    return mosquitoes

## Calculate the mosquito population
We need to supply initial mosquito numbers, survival probability, linear parameters, rainfall and number of averaging days to the population function.

### First reshape the survival probability and rainfall arrays to match what is required by the function

In [89]:
p_array = df['P'].values.reshape((1,1,len(df)))
r_array = df['rainfall'].values.reshape((1,1,len(df)))
print(p_array.shape, r_array.shape)

(1, 1, 7306) (1, 1, 7306)


In [ ]:
m_array = calc_mosquito_pop(0.0, p_array, r_array, 1, params["rainfall_multiplier"], params["rainfall_offset"])
df['mosquitoes'] = m_array[0,0,:]

In [90]:
df.head(15)

day  month  year  longitude  latitude      rainfall  temperature  \
0     1      1  2001       29.0     -24.0  6.687416e+00    22.233392   
1     1      1  2002       29.0     -24.0  4.647458e-03    25.498193   
2     1      1  2003       29.0     -24.0  0.000000e+00    21.804725   
3     1      1  2004       29.0     -24.0  1.721056e+00    20.897620   
4     1      1  2005       29.0     -24.0  2.637308e+00    24.388575   
5     1      1  2006       29.0     -24.0  0.000000e+00    22.960608   
6     1      1  2007       29.0     -24.0  2.654061e-01    18.466405   
7     1      1  2008       29.0     -24.0  0.000000e+00    22.128403   
8     1      1  2009       29.0     -24.0  4.616548e+00    21.570000   
9     1      1  2010       29.0     -24.0  4.581932e-03    25.462178   
10    1      1  2011       29.0     -24.0  3.561104e+00    21.459982   
11    1      1  2012       29.0     -24.0  7.702660e-01    22.718991   
12    1      1  2013       29.0     -24.0  1.726238e+01    23.664625   
13    1      1  2014       29.0     -24.0  6.841875e-07    21.930809   
14    1      1  2015       29.0     -24.0  4.936545e-02    19.916315   

           P  gono_len   sporo_len  mosquitoes  
0   0.859685  3.795957   26.220107    0.000000  
1   0.786650  3.242670   14.803566    6.687416  
2   0.866742  3.889558   29.174253    8.606687  
3   0.879735  4.109866   38.307299    9.690460  
4   0.815299  3.404381   17.374765   10.628313  
5   0.846370  3.650314   22.376287   10.875338  
6   0.901573  4.908559  237.990339   11.046293  
7   0.861468  3.818317   26.886910   11.575586  
8   0.870356  3.943516   31.092437   11.386474  
9   0.787642  3.247576   14.875015   11.680552  
10  0.871990  3.969507   32.081096   10.793785  
11  0.850981  3.696991   23.521980   11.184621  
12  0.831867  3.523079   19.595296   10.752534  
13  0.864727  3.861383   28.238460   11.748188  
14  0.890826  4.389422   57.923680   12.962490

# Bring it all together: Calculate R0

### Define function to calculate R0

In [91]:
def calculate_R0(mosquitoes, p, Gdays, Sdays, r, HIA, HBI, b, c):
# mosquitoes, p, GDays and SDays are multidimensional 
# arrays of the same shape e.g. [x, y, month]
# HBI, r and HIA are constants
# Calculates element-wise R0
    if not ((mosquitoes.shape==p.shape)&
            (p.shape==Gdays.shape)&
            (p.shape==Sdays.shape)):
        print("error: supplied array shapes do not match")
        return None
    dims = p.shape
    TP = np.empty(dims)
    R0 = np.empty(dims)
    a = np.empty(dims)
    mu = np.empty(dims)
    idx = p>0.0
    a[idx] = HBI/Gdays[idx]
    mu[idx] = -1.0*np.log(p[idx])
    TP[idx] = np.divide(np.square(a[idx])*b*c*np.exp(-1.0*mu[idx]*Sdays[idx] - r*HIA),
                   (mu[idx]*r))
    R0[idx] = np.multiply(mosquitoes[idx], TP[idx])
    return R0

### Reshape arrays

In [94]:
m_array = df['mosquitoes'].values.reshape(1,1,len(df))
p_array = df['P'].values.reshape((1,1,len(df)))
g_array = df['gono_len'].values.reshape((1,1,len(df)))
s_array = df['sporo_len'].values.reshape((1,1,len(df)))


### Apply the function

In [96]:
R0 = calculate_R0(m_array, p_array, g_array, s_array, params["r"], \
                             params["hia"], params["hbi"], params["b"], params["c"])
df['R0'] = R0[0,0,:]

## Plot time series

In [97]:
def datetime_from_components(year, month, day):
    dt = np.datetime64(str(year) + '-' + str(month).zfill(2) + '-' + str(day).zfill(2))
    return dt

In [100]:
df['datetime'] = pd.to_datetime(df[['year', 'month', 'day']])

In [104]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
infostr = 'location: ' + str(lon) + ' E, ' + str(lat) + ' N'
print('Analysis for ' + infostr)

fig = make_subplots(rows=4, cols=1, shared_xaxes=True, \
                   subplot_titles = ['Rainfall', "Temperature", \
                                     "Model Mosquitoes", "Model R0"],
                   vertical_spacing = 0.05)
times = df['datetime']
fig.add_trace(
    go.Scatter(x=times, y=df['rainfall'], showlegend=False, mode='markers'), 
    row=1, col=1) 
fig.add_trace(
    go.Scatter(x=times, y=df['temperature'], showlegend=False, mode='markers'), 
    row=2, col=1)
fig.add_trace(
    go.Scatter(x=times, y=df['mosquitoes'], showlegend=False, mode='markers'), 
    row=3, col=1)
fig.add_trace(
    go.Scatter(x=times, y=df['R0'], showlegend=False, mode='markers'), 
    row=4, col=1) 
fig.update_layout(
    autosize=False,
    width=800,
    height=900)
fig.update_yaxes(title_text="Rainfall [mm]", row=1, col=1)
fig.update_yaxes(title_text="Temperature [degC]", row=2, col=1)
fig.update_yaxes(title_text="Mosquito population size", row=3, col=1)
fig.update_yaxes(title_text="R0", row=4, col=1)
fig.for_each_yaxis(lambda axis: axis.title.update(font=dict(size=12)))

fig.show()


Analysis for location: 29.0 E, -24.0 N


## Climate driver sensitivities 

In [103]:
print('Analysis for ' + infostr)
fig = make_subplots(rows=2, cols=2, shared_xaxes=False, \
                   subplot_titles = ['Rainfall and Mosquitoes',  \
                                     "Temperature and survival",\
                                     "Rainfall and R0",\
                                     "Temperature and R0"],
                   vertical_spacing = 0.1)

fig.add_trace(
    go.Scatter(x=df['rainfall'], y=df['mosquitoes'], showlegend=False, mode="markers"), 
    row=1, col=1) 
fig.add_trace(
    go.Scatter(x=df['temperature'], y=df['P'], showlegend=False, mode="markers"), 
    row=1, col=2)
fig.add_trace(
    go.Scatter(x=df['rainfall'], y=df['R0'], showlegend=False, mode="markers"), 
    row=2, col=1)
fig.add_trace(
    go.Scatter(x=df['temperature'], y=df['R0'], showlegend=False, mode="markers"), 
    row=2, col=2) 
fig.update_layout(
    autosize=False,
    width=800,
    height=800)
fig.for_each_yaxis(lambda axis: axis.title.update(font=dict(size=12)))

fig.show()

Analysis for location: 29.0 E, -24.0 N
